## このノートブックでは、「Perceptron」手法を用いて手書き数字を認識（2項分類）する機械学習モデルを作成し、その精度を評価する。

Author: Karol Nowakowski

In [ ]:
import numpy as np
from sklearn.datasets import fetch_openml
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import japanize_matplotlib

In [ ]:
def visualize_mnist_digit(digit, cmap="Wistia", colorbar_label="画素値"):
  """
  MNISTデータの画像1枚を表示する。
  """
  image = digit.reshape(28, 28)
  plt.imshow(image, cmap=cmap)
  plt.axis("off")
  plt.colorbar(label=colorbar_label)
  plt.show()

In [ ]:
class Perceptron:
    """
    パーセプトロンを実装したクラス
    """

    def __init__(self, learning_rate=0.1, max_epochs=1000):
        """
        初期化（ハイパーパラメータの設定）
        """
        self.learning_rate = learning_rate # 学習率
        self.max_epochs = max_epochs # 学習回数

    def train(self, X, y):
        """
        学習を実行する。
        入力：
        X - 学習サンプル（画像）の配列
        y - 各画像に対する正解ラベル（「0」若しくは「1」）
        """
        self.weights = np.random.rand(X.shape[1]) # 重みを乱数に初期化する

        for _ in range(self.max_epochs):
            for i in range(X.shape[0]): # 各学習サンプル（画像）に対して処理を行う
                prediction = self.predict(X[i]) # 予測を行う
                difference = y[i] - prediction # 正解と予測値の差を求める
                for j in range(X.shape[1]): # 重みを更新する
                    self.weights[j] += self.learning_rate * difference * X[i][j]

    def activation_function(self, input_value):
        """
        パーセプトロンへの入力の加重和を受け取り、活性化関数を適用する。
        ここでは、負の値の場合は0、正の値をの場合は1を返す「ステップ関数」を使用する。
        """
        if input_value >= 0:
            return 1
        return 0

    def predict(self, x):
        """
        与えられた画像データ点(x)に書いてある数字を予測する。具体的には入力とモデルの重みの加重総和を求めて、
        最後に活性化関数を適用する。重みとxはどちらもベクトルであるため、内積が使用される。
        """
        input_value = np.dot(self.weights, x) # 入力と重みの加重総和（内積）
        prediction = self.activation_function(input_value) # 活性化関数を適用した予測値
        return prediction

    def calculate_accuracy(self, X_test, y_test):
        """
        評価データにおけるモデルの予測の適合率(accuracy)を求める。
        凡例：
        tp (True Positive) - 陽性のもの（ここでは1）を正しく陽性と予測した回数
        tn (True Negative) - 陰性のもの（ここでは0）を正しく陰性と予測した回数
        fp (False Positive) - 陰性のもの（0）を誤って陽性（1）と予測した回数
        fn (False Negative) - 陽性のもの（1）を誤って陰性（0）と予測した回数
        """
        tp, tn, fp, fn = 0, 0, 0, 0 # 初期化
        for sample, label in zip(X_test, y_test):
            prediction = self.predict(sample) # 予測を行う
            if prediction == label:
                if prediction == 1:
                    tp += 1
                else:
                    tn += 1
            else:
                if prediction == 1:
                    fp += 1
                else:
                    fn += 1
        accuracy = (tp + tn)/(tp + tn + fp + fn)
        return accuracy

    def visualize(self):
        """
        モデルのパラメーター（MNIST画像の各ピクセルに該当する重み）を可視化する。
        """
        visualize_mnist_digit(self.weights, colorbar_label="重み")

In [ ]:
# MNISTデータを読み込みする
mnist = fetch_openml('mnist_784', as_frame = False)
X = mnist.data # 画像データ（各画像は各ピクセルの輝度を0~255の数値で表したベクトルとして保管されている）
y = mnist.target # 各画像に対する正解ラベル（0~9の数字）

# 正解ラベルが「0」か「1」のデータのみを残す
X = X[np.logical_or(y == '0', y == '1')]
y = y[np.logical_or(y == '0', y == '1')]

# 正解ラベルを文字列から数字に変換（"0"なら0、"1"なら1）
y = np.where((y == '0'), 0, 1)

# データを教師データ（80%)と評価データ（20%）に分ける
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [ ]:
# 教師データの先頭の画像5枚を表示してみる
for n in range(5):
    visualize_mnist_digit(X_train[n])

In [ ]:
# 評価データの先頭の画像5枚を表示してみる
for n in range(5):
    visualize_mnist_digit(X_test[n])

In [ ]:
# パーセプトロン分類機を作成し用意したデータで学習を行う
perceptron = Perceptron(learning_rate=0.1, max_epochs=1)
perceptron.train(X_train, y_train)
# 評価データでの適合率を確認する
accuracy = perceptron.calculate_accuracy(X_test, y_test)
print("適合率： {:.2%}".format(accuracy))

In [ ]:
# 学習されたモデルの重みを可視化する
perceptron.visualize()